In [1]:
import numpy as np
import plotly.graph_objects as go
def save_figure_to_file(fig, path, file_name):
    fig.write_image(path + '/' + file_name + '.svg')

In [2]:
n = 4

Z = np.random.standard_normal((n,n))

Q, R = np.linalg.qr(Z,mode='complete')

# test
np.testing.assert_array_less(np.eye(n) - np.dot(Q,Q.T), 1e-14)

d = np.random.random((n,))
d = np.sort(d)
D = np.diag(d)

H = np.dot(Q, np.dot(D,Q.T))
U, S, VT = np.linalg.svd(H, full_matrices=True)

# test symmetry
np.linalg.norm(H - H.T)

# test evals
w, v = np.linalg.eig(H)
w = np.sort(w)
np.testing.assert_array_less(w-d, 1e-14)

beta = 0.1

D = np.diag([beta**k for k in range(n)])

Hb = np.dot(D, np.dot(H, D))

U, S, VT = np.linalg.svd(Hb, full_matrices=True)

for i in range(n):
    if U[i,i] < 0:
        U[:,i] = -U[:,i]
        VT[i,:] = -VT[i,:]

print('Hb=')
print(Hb)
print('U=')
print(U)
print('V=')
print(VT.T)
print('Sigma=')
print(S/S[0])

Hb=
[[ 4.54416584e-01 -2.61706551e-03  1.76251093e-04  1.12166054e-04]
 [-2.61706551e-03  4.63335400e-03 -9.70238013e-05 -4.30875236e-06]
 [ 1.76251093e-04 -9.70238013e-05  4.80289185e-05  2.78986234e-07]
 [ 1.12166054e-04 -4.30875236e-06  2.78986234e-07  5.24546059e-07]]
U=
[[ 9.99982967e-01  5.82537343e-03 -2.67744215e-04 -2.41326421e-04]
 [-5.81829295e-03  9.99762375e-01  2.09957620e-02  7.20330978e-04]
 [ 3.89126203e-04 -2.09912053e-02  9.99773445e-01 -3.50393004e-03]
 [ 2.46878465e-04 -7.92310800e-04  3.48797011e-03  9.99993573e-01]]
V=
[[ 9.99982967e-01  5.82537343e-03 -2.67744215e-04 -2.41326421e-04]
 [-5.81829295e-03  9.99762375e-01  2.09957620e-02  7.20330978e-04]
 [ 3.89126203e-04 -2.09912053e-02  9.99773445e-01 -3.50393004e-03]
 [ 2.46878465e-04 -7.92310800e-04  3.48797011e-03  9.99993573e-01]]
Sigma=
[1.00000000e+00 1.01668599e-02 1.01104566e-04 1.08574231e-06]


In [3]:
x0 = np.random.standard_normal((n,1))

D = np.diag([beta**(-k) for k in range(n)])

alpha = 1

w, v = np.linalg.eig( alpha * Hb )
print(w)

w, v = np.linalg.eig( alpha * np.dot(D, Hb) )
print(w)

x = x0.copy()
print('|x0|=',np.linalg.norm((x)))

k_iter = 10000
print('number of iterations=',k_iter)
G = np.eye(n) - alpha * np.dot(D, Hb)
norm_x_0 = np.zeros(1 + int((k_iter-1)/100))
for k in range(k_iter):
    x = np.dot(G, x)
    if k%100 == 0:
        norm_x_0[int(k/100)] = np.linalg.norm((x))

print('x=',np.linalg.norm((x)))
        
x = x0.copy()
k_iter = int(k_iter/beta**(n-1))
print('number of iterations=',k_iter)
G = np.eye(n) - alpha * Hb
norm_x_1 = np.zeros(1 + int((k_iter-1)/100))
for k in range(k_iter):
    x = np.dot(G, x)
    if k%100 == 0:
        norm_x_1[int(k/100)] = np.linalg.norm((x))     

print('x=',np.linalg.norm((x)))

[4.54431907e-01 4.62014553e-03 4.59451407e-05 4.93395951e-07]
[0.45461959 0.04638965 0.00457504 0.00049328]
|x0|= 1.4811996991389953
number of iterations= 10000
x= 0.0016325646448890165
number of iterations= 9999999
x= 0.0002831662055764619


In [4]:
beta = 0.1
n = 4
# beta = 0.9
# n = 100
m = n-1
print('Estimated condition number: {:.2e}\n'.format(beta**(2*m)))
print('Estimated number of iterations with Adagrad: {:.2e}\n'.format(beta**(-m)))
print('Estimated number of iterations without Adagrad: {:.2e}\n'.format(beta**(-2*m)))

Estimated condition number: 1.00e-06

Estimated number of iterations with Adagrad: 1.00e+03

Estimated number of iterations without Adagrad: 1.00e+06



In [5]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=norm_x_1,name='Gradient Descent'))
fig.add_trace(go.Scatter(y=norm_x_0,name='Adagrad'))
fig.update_layout(height=400, width=600, xaxis_type="log", yaxis_type="log", 
                  xaxis_title='iteration', yaxis_title='error')
fig.show()

In [6]:
save_figure_to_file(fig,'../Slides/Deep_Learning','fig6')